Description: Despite the popularity of autonomous vehicles, the robustness of these vehicles degrades when operating in the rural areas or new environments. To address this challenge, your task is to build an AI system that has the following capabilities during the vehicle navigation: (1) detect known objects in the video; (2) detect novel objects in the video; and (3) make decisions to avoid collisions on the road. Note that the second and third capabilities are crucial for any autonomous vehicle to improve its robustness.

In [ ]:
# Turn off warning
import warnings
warnings.filterwarnings('ignore')

# Video processing

In [ ]:
import moviepy.editor
from moviepy.video.io.ffmpeg_tools import ffmpeg_extract_subclip
import numpy as np
from moviepy.editor import ImageSequenceClip
import cv2

def create_video_from_images(images, video_name, fps):
    clip = ImageSequenceClip(images, fps=fps)
    clip.write_videofile(video_name)

def clip_vdieo(video_path, start_time, end_time, output_path):
    ffmpeg_extract_subclip(video_path, start_time, end_time, targetname=output_path)

def reszie_video(video_path, output_path, width=640, height=480):
    clip = moviepy.editor.VideoFileClip(video_path)
    resized_clip = clip.resize(width=width)
    resized_clip.write_videofile(output_path)

# Download dash cam video

In [ ]:
!wget -O video.mp4 https://download.ifi.uzh.ch/rpg/web/data/E2VID/datasets/driving_gen3/external_videos/back8.mp4

--2024-10-10 16:03:44--  https://download.ifi.uzh.ch/rpg/web/data/E2VID/datasets/driving_gen3/external_videos/back8.mp4
Resolving download.ifi.uzh.ch (download.ifi.uzh.ch)... 130.60.61.200
Connecting to download.ifi.uzh.ch (download.ifi.uzh.ch)|130.60.61.200|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 52029131 (50M) [video/mp4]
Saving to: ‘video.mp4’

video.mp4           100%[===================>]  49.62M  4.40MB/s    in 12s     

2024-10-10 16:03:57 (4.16 MB/s) - ‘video.mp4’ saved [52029131/52029131]



In [ ]:
clip_vdieo("video.mp4", 5, 15, "video_clip.mp4")
reszie_video("video_clip.mp4", "video_resized.mp4")
moviepy.editor.ipython_display("video_resized.mp4")

Moviepy - Running:
>>> "+ " ".join(cmd)
Moviepy - Command successful
Moviepy - Building video video_resized.mp4.
Moviepy - Writing video video_resized.mp4



Moviepy - Done !
Moviepy - video ready video_resized.mp4


# 1. Detect known objects in the video

In [ ]:
!git clone https://github.com/ultralytics/yolov5  # clone
%cd yolov5
!pip install -r requirements.txt  # install
%cd ..

fatal: destination path 'yolov5' already exists and is not an empty directory.
/content/yolov5
/content


In [ ]:
import cv2
from ultralytics import YOLO
import numpy as np

# Load the YOLOv5 model
model = YOLO("yolov5s.pt")

# Open the video file
video_path = "video_resized.mp4"
cap = cv2.VideoCapture(video_path)

# Get video properties
fps = cap.get(cv2.CAP_PROP_FPS)

images = []

while cap.isOpened():
    success, frame = cap.read()
    if success:
        # Run YOLOv5 inference on the frame
        results = model(frame, verbose=False)

        # Annotate the frame with bounding boxes and labels
        images.append(results[0].plot()[..., ::-1])
    else:
        break

# Release resources
cap.release()

# Save the annotated video
create_video_from_images(images, "output_known.mp4", fps)

PRO TIP 💡 Replace 'model=yolov5s.pt' with new 'model=yolov5su.pt'.
YOLOv5 'u' models are trained with https://github.com/ultralytics/ultralytics and feature improved performance vs standard YOLOv5 models trained with https://github.com/ultralytics/yolov5.

Moviepy - Building video output_known.mp4.
Moviepy - Writing video output_known.mp4



Moviepy - Done !
Moviepy - video ready output_known.mp4


In [ ]:
moviepy.editor.ipython_display("output_known.mp4")

# 2. Detect novels objects in the video

In [ ]:
def get_novel_objects(img, results, min_area=2500, max_area=5000):
    img1 = img.copy()
    # Get bounding box list
    confs = results[0].boxes.conf
    boxes = results[0].boxes.xyxy

    # Convert to numpy
    confs = confs.cpu().numpy()
    boxes = boxes.cpu().numpy()

    indexes = np.where((confs < 0.25))
    boxes = boxes[indexes]

    areas = []

    for box in boxes:
        x1, y1, x2, y2 = box
        areas.append((x2 - x1) * (y2 - y1))

    areas = np.array(areas)
    indexes = np.where((areas >= min_area) & (areas <= max_area))
    boxes = boxes[indexes]

    return boxes

def draw_novel_objects(img, boxes):
    img1 = img.copy()

    # Draw boxes on image
    for box in boxes:
        x1, y1, x2, y2 = box
        # If box area greater than min_area
        cv2.rectangle(img1, (int(x1), int(y1)), (int(x2), int(y2)), (0, 255, 0), 2)
        # Put text
        cv2.putText(img1, f"Novel object", (int(x1), int(y1) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0))

    return img1[..., ::-1]

In [ ]:
# Open the video file
video_path = "video_resized.mp4"
cap = cv2.VideoCapture(video_path)


# Get video properties
fps = cap.get(cv2.CAP_PROP_FPS)

images = []

while cap.isOpened():
    success, frame = cap.read()
    if success:
        # Run YOLOv5 inference on the frame
        results = model(frame, conf=0.1, iou=0.2, agnostic_nms=True)

        novel_objects = get_novel_objects(frame, results, min_area=2000, max_area=10000)
        images.append(draw_novel_objects(frame, novel_objects))
    else:
        break

# Release resources
cap.release()

# Save the annotated video
create_video_from_images(images, "output_novel.mp4", fps)

Moviepy - Building video output_novel.mp4.
Moviepy - Writing video output_novel.mp4



Moviepy - Done !
Moviepy - video ready output_novel.mp4


In [ ]:
moviepy.editor.ipython_display("output_novel.mp4")

# 3. Make decisions to avoid collisions on the road

In [ ]:
# Draw a horizontal line on the image
def draw_line(img, safe_boundary=(100, 540, 340)):
    img1 = img.copy()
    cv2.line(img1, (safe_boundary[0], safe_boundary[-1]), (safe_boundary[1], safe_boundary[-1]), (0, 0, 255), 2)
    return img1

In [ ]:
def check_collision(bboxes, safe_boundary=(100, 540, 340)):
    for bbox in bboxes:
        x1, y1, x2, y2 = bbox
        if y2 >= safe_boundary[-1] and x1 >= safe_boundary[0] and x2 <= safe_boundary[1]:
            return True
    return False

In [ ]:
# Open the video file
video_path = "video_resized.mp4"
cap = cv2.VideoCapture(video_path)

# Get video properties
fps = cap.get(cv2.CAP_PROP_FPS)

images = []
safe_boundary = safe_boundary=(100, 540, 340)
while cap.isOpened():
    success, frame = cap.read()
    if success:
        # Run YOLOv5 inference on the frame
        results = model(frame, conf=0.1, iou=0.2, agnostic_nms=True)
        novel_objects = get_novel_objects(frame, results, min_area=2000, max_area=10000)

        results = model(frame, verbose=False)
        known_objects = results[0].boxes.xyxy.cpu().numpy()

        image = results[0].plot()
        image = draw_line(image, safe_boundary)
        image = draw_novel_objects(image, novel_objects)

        image1 = image.copy()
        if check_collision(novel_objects, safe_boundary=safe_boundary) or check_collision(known_objects, safe_boundary=safe_boundary):
            image1 = cv2.putText(image1, "Collision detected", (200, 100), cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 0, 0), 2)

        images.append(image1)

    else:
        break

# Release resources
cap.release()

# Save the annotated video
create_video_from_images(images, "output.mp4", fps)

Moviepy - Building video output.mp4.
Moviepy - Writing video output.mp4



Moviepy - Done !
Moviepy - video ready output.mp4


In [ ]:
moviepy.editor.ipython_display("output.mp4")